In [31]:
# %load http://che.byu.edu/imports.py
import numpy             as np
import matplotlib.pyplot as plt
%matplotlib inline
from scipy.optimize      import fsolve, curve_fit
from scipy.integrate     import odeint, quad
from scipy.interpolate   import interp1d
from scipy.misc          import derivative
import scipy.constants   as const
import sympy             as sp
sp.init_printing()
import glob
import time
#import pint; u = pint.UnitRegistry()

Problem 13.10 for ChE 733

In [97]:
Tg = 1800   #K
Ptot = 1    #atm
PO2g = .1   #atm
dpm = 500    #particle diameter in microns
dp = dpm*1e-4 #particle diameter in cm
Tp = 1800   #K
Nu = 2       #Nusselt number
Sh = 2       #Sherwood number
eps = 0.8    #particle emissivity
sigma = 1.3552E-15   #StefanBoltzman constant in kcal/cm^2/K^4
Twall = 1000 #Wall temperature in K
print("Twall = ",Twall)
Carbonfrac = 0.8
n = 0.5
Rcal = 1.987
Rgas = 82.05    #cm^3-atm/gmol/K
Ea = -5.9+0.355*Carbonfrac*100   #Activation Energy in kcal/gmol
lnk_1750 = (2.8-0.076*Carbonfrac*100)
A = np.exp(lnk_1750 + Ea*1000/(Rcal*1750))   #g-C/cm^2/s/atm^0.5
print('Ea (kcal/mol) = ',Ea)
print('A g-C/cm^2/s/atm^0.5', A)
COtoCO2 = 1e6
DelH_CO = 26.4   #kcal/mol C
DelH_CO2 = 94.1  #kcal/mol C
net_DelH = COtoCO2/(1+COtoCO2)*DelH_CO+1/(1+COtoCO2)*DelH_CO2
print("net_DelH = ",net_DelH)
stoich = COtoCO2/(1+COtoCO2)*2+1/(1+COtoCO2)*1   #moles C per mole O2

Twall =  1000
Ea (kcal/mol) =  22.5
A g-C/cm^2/s/atm^0.5 24.30374678143053
net_DelH =  26.400067699932297


Calculate the diffusivity

In [98]:
def diff(Tfilm,Ptot):
#   Uses correlation from Mitchell report. 
#   diffusivity is in cm^2/s
    diff = 0.00001523*Tfilm**1.67/Ptot
    return diff

Calculate the thermal conductivity

In [99]:
def kg(Tfilm):
    kg =(0.00000076893*Tfilm**0.7722)/1000   #kcal/cm/s/K
    return kg

Calculate the actual diffusion rate

In [100]:
def ActDiffrate(Tg,Tp,PO2s):
    Tfilm = (Tg + Tp)/2
# Reaction Rate calculation
    km = Sh*diff(Tfilm,Ptot)/dp     #Mass transfer coefficient
#    print('PO2g',PO2g,'PO2s',PO2s,'Tg',Tg)
    Diffrate = km*(PO2g/(0.08205*Tg*1000)-PO2s/(0.08205*Tg*1000))*stoich*12
    return Diffrate

Calculate the surface reaction rate

In [101]:
def ActRxnrate(Tp,PO2s):
    Rxnrate = A*np.exp(-Ea*1000/(Rcal*Tp))*(PO2s)**n
    return Rxnrate

This function sets the diffusion rate equal to the surface reaction rate by adjusting $P_{O2,s}$, and also calculates the particle temperature by setting the energy balance to zero

In [102]:
def Balances(Variables):
# Set diffusion rate = surface reaction rate
    Tp = Variables[0]
    PO2s = Variables[1]
    Drate = ActDiffrate(Tg,Tp,PO2s)
    Srate = ActRxnrate(Tp,PO2s)
    Tfilm = (Tg + Tp)/2
    Deltarate =Drate-Srate

# Energy balance calculation
    h = Nu*kg(Tfilm)/dp
    qconv = h*(Tg-Tp)
    qrad = eps*sigma*(Twall**4 - Tp**4)
    qrxn = Drate*net_DelH/12   #reaction rate times the heat of reaction
    Netq = qconv + qrad + qrxn
    Balances = abs(Deltarate) + abs(Netq)
    return [Deltarate,Netq]

Now solve the rate and energy function simultaneously

In [103]:
Tp0 = 1800
PO2s0 = .001
Variables = np.array([Tp0,PO2s0])
#print(Variables)
#Tnew = fsolve(Netq,Tp)
#print(Tp,Tnew)
solution = fsolve(Balances,Variables)
Tp = solution[0]
PO2s = max(solution[1],1e-6)
print('Tp =',Tp)
print('PO2s =',PO2s)

Tp = 1632.1212834039684
PO2s = 0.009232766443088302


In [104]:
def MaxDiffrate(Tp):
    Tfilm1 = (Tg + Tp)/2
    km = Sh*diff(Tfilm1,Ptot)/dp     #Mass transfer coefficient
    MaxDiffrate = km*(PO2g/(0.08205*Tg*1000))*stoich*12
    return MaxDiffrate


Now define the function to calculate the maximum burning rate and particle temperature

In [105]:
def Netq(Tp):
    Tfilm1 = (Tg + Tp)/2
#    km = Sh*diff(Tfilm1,Ptot)/dp     #Mass transfer coefficient
#    MaxDiffrate = km*(PO2g/(0.08205*Tg*1000))*2*12
    h = Nu*kg(Tfilm1)/dp
    qconv = h*(Tg-Tp)
    qrad = eps*sigma*(Twall**4 - Tp**4)
    qrxn = MaxDiffrate(Tp)*net_DelH/12   #reaction rate times the heat of reaction
    Netq = qconv + qrad + qrxn
#    print (Netq,eps,sigma,Twall,Tg,Tfilm)
#    print(qconv,qrad,qrxn)
    return Netq

Solve for the maximum particle temperature under film diffusion limitations

In [106]:
Tmax = fsolve(Netq,Tp)
print(Tp,Tmax)

1632.1212834039684 [1651.71956826]


Now calculate the ratio of the actual rate to the maximum possible diffusion rate

In [107]:
    Actrate = ActRxnrate(Tp,PO2s)
    Maxrate = MaxDiffrate(Tmax)
    Chi = Actrate/Maxrate
    print('Tp =',Tp)
    print('PO2s =',PO2s)   
    print('actual reaction rate (g Carbon/cm^2/s) =',Actrate)
    print('maxim rate (g Carbon/cm^2/s) = ',Maxrate)
    print('chi factor =',Chi)

Tp = 1632.1212834039684
PO2s = 0.009232766443088302
actual reaction rate (g Carbon/cm^2/s) = 0.0022657835590534983
maxim rate (g Carbon/cm^2/s) =  [0.00252011]
chi factor = [0.89908219]
